# Notebook 4: Compute d3 for testing facilities and residence centroids and visualize routes

## Introduction to Noteboook 4

In this notebook, we will:

1. compute `d3` using several methods
2. Obtain `d3_total` by adding `d1`, `d2` and `d3` from the selected method
3. Display residence centroids, testing facilities, a sample of 5 routes.

### Note

This notebook loads two graphs (projected and unprojected) and hence would consume a lot more memory. You should shut down other notebooks if you have memory constraints.

## Data sources

In [1]:
import pandas as pd, geopandas as gpd, folium, os

pd.options.display.float_format = '{:.10f}'.format

### Testing Facilities, Target Parish, Parishes, Residence Centroids

In [2]:
filtered_testing_sites_4326_gdf = gpd.read_file('data/filtered_testing_sites_4326_gdf.gpkg')
parish_gdf = gpd.read_file('data/parish_gdf.gpkg')
parishes_gdf = gpd.read_file('data/parishes_gdf.gpkg')
residential_centroids_4326_gdf = gpd.read_file('data/residential_centroids_4326_gdf.gpkg')

In [3]:
residential_centroids_4326_gdf.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 214 entries, 0 to 213
Data columns (total 14 columns):
 #   Column       Non-Null Count  Dtype   
---  ------       --------------  -----   
 0   parish_name  214 non-null    object  
 1   building     214 non-null    object  
 2   lat          214 non-null    float64 
 3   lon          214 non-null    float64 
 4   prj_lat      214 non-null    float64 
 5   prj_lon      214 non-null    float64 
 6   r_node       214 non-null    int64   
 7   d1           214 non-null    float64 
 8   d1_euc       214 non-null    float64 
 9   r_node_lat   214 non-null    float64 
 10  r_node_lon   214 non-null    float64 
 11  r_node_x     214 non-null    float64 
 12  r_node_y     214 non-null    float64 
 13  geometry     214 non-null    geometry
dtypes: float64(10), geometry(1), int64(1), object(2)
memory usage: 23.5+ KB


In [4]:
residential_centroids_4326_gdf.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [5]:
residential_centroids_4326_gdf

parish_name     building          lat           lon          prj_lat  \
0        Kisugu  residential 0.3050501833 32.6082495446 33718.0074585697   
1        Kisugu    dormitory 0.3053414841 32.6082456333 33750.2057395246   
2        Kisugu       duplex 0.3045664193 32.6084960943 33664.5347349995   
3        Kisugu  residential 0.3045408000 32.6083606500 33661.7035135770   
4        Kisugu  residential 0.3046784338 32.6080187078 33676.9179346887   
..          ...          ...          ...           ...              ...   
209      Kisugu        house 0.3086906479 32.6082211451 34120.3978818522   
210      Kisugu        house 0.3088099936 32.6081564965 34133.5897534508   
211      Kisugu        house 0.3087290884 32.6080501563 34124.6475147437   
212      Kisugu        house 0.3090996240 32.6081822843 34165.6032674131   
213      Kisugu        house 0.3101291814 32.6087909503 34279.4005037105   

              prj_lon      r_node            d1            d1_euc  \
0   456408.2543575270  6227266298 50.2749796310 457652.0497852722   
1   456407.8202964029   579993314 32.3712105445 457653.9902755943   
2   456435.6874821403  6227266298 21.9934580881 457675.4720391054   
3   456420.6156729474  6227266298  9.1897739823 457660.2328089129   
4   456382.5662585886  6227266299 29.8734513255 457623.4058550270   
..                ...         ...           ...               ...   
209 456405.1089029149   579993370 33.3112340446 457678.7355605431   
210 456397.9155612630  1460122475 41.2411144888 457672.5459082319   
211 456386.0821231636   579993372 46.3235329624 457660.0785776891   
212 456400.7863013543  6226990677 12.9739007177 457677.7973456007   
213 456468.5204023762   579993409 28.5202411754 457753.8502483932   

      r_node_lat    r_node_lon          r_node_x         r_node_y  \
0   0.3045983000 32.6083010000 456413.9782893857 33668.0593837221   
1   0.3055411000 32.6084585000 456431.5080539904 33772.2689535378   
2   0.3045983000 32.6083010000 456413.9782893857 33668.0593837221   
3   0.3045983000 32.6083010000 456413.9782893857 33668.0593837221   
4   0.3045855000 32.6082708000 456410.6177021883 33666.6446875843   
..           ...           ...               ...              ...   
209 0.3084251000 32.6083627000 456420.8594871131 34091.0455836289   
210 0.3091566000 32.6080193000 456382.6502965369 34171.9016473888   
211 0.3083446000 32.6082158000 456404.5127182511 34082.1483045059   
212 0.3092163000 32.6081950000 456402.2017287260 34178.4997268183   
213 0.3103850000 32.6088244000 456472.2435919398 34307.6766777122   

                     geometry  
0    POINT (32.60825 0.30505)  
1    POINT (32.60825 0.30534)  
2    POINT (32.60850 0.30457)  
3    POINT (32.60836 0.30454)  
4    POINT (32.60802 0.30468)  
..                        ...  
209  POINT (32.60822 0.30869)  
210  POINT (32.60816 0.30881)  
211  POINT (32.60805 0.30873)  
212  POINT (32.60818 0.30910)  
213  POINT (32.60879 0.31013)  

[214 rows x 14 columns]

In [6]:
filtered_testing_sites_4326_gdf.shape

(16, 17)

In [7]:
filtered_testing_sites_4326_gdf.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 16 entries, 0 to 15
Data columns (total 17 columns):
 #   Column       Non-Null Count  Dtype   
---  ------       --------------  -----   
 0   FACILITY     16 non-null     object  
 1   CITY         16 non-null     object  
 2   ADDRESS      16 non-null     object  
 3   LAT          16 non-null     float64 
 4   LON          16 non-null     float64 
 5   COORDINATES  16 non-null     object  
 6   NOTES        2 non-null      object  
 7   PRJ_LAT      16 non-null     float64 
 8   PRJ_LON      16 non-null     float64 
 9   t_node       16 non-null     int64   
 10  d2           16 non-null     float64 
 11  d2_euc       16 non-null     float64 
 12  t_node_lat   16 non-null     float64 
 13  t_node_lon   16 non-null     float64 
 14  t_node_x     16 non-null     float64 
 15  t_node_y     16 non-null     float64 
 16  geometry     16 non-null     geometry
dtypes: float64(10), geometry(1), int64(1), object(5)
memory usage: 2.2+

In [8]:
filtered_testing_sites_4326_gdf.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [9]:
filtered_testing_sites_4326_gdf

FACILITY     CITY  \
0          Central Public Health Laboratory  Kampala   
1   Infectious Disease Institute Laboratory  Kampala   
2                       Makerere University  Kampala   
3                       Mild May Laboratory  Kampala   
4     Joint Clinical Research Center (JCRC)  Kampala   
5                           MBN Laboroatory  Kampala   
6            Medipal International Hospital  Kampala   
7                   Test and Fly Laboratory  Kampala   
8                   Uganda Cancer Institute  Kampala   
9                            IOM Laboratory  Kampala   
10                             ANCA Biotech  Kampala   
11                              Case Clinic  Kampala   
12                MSF-Epicentre Lab-Mbarara  Kampala   
13                      Lancet Laboratories  Kampala   
14                        ATCG Laboratories  Kampala   
15                            Same Day Labs  Kampala   

                                              ADDRESS          LAT  \
0          7/11, Plot 113 Buganda Rd, Kampala, Uganda 0.3312460000   
1                      P.O.Box 22418, Kampala, Uganda 0.3391550000   
2                      University Rd, Kampala, Uganda 0.3337660000   
3                           6HG2+QJH, Kampala, Uganda 0.2272610000   
4                      P.o.Box 10005, Kampala, Uganda 0.2471060000   
5                Plot 28 Nakasero Rd, Kampala, Uganda 0.3244010000   
6           John Babiha (Acacia) Ave, Kampala, Uganda 0.3267710000   
7                    Yusuf Lule Road, Kampala, Uganda 0.3280000000   
8               Upper Mulago Hill Rd, Kampala, Uganda 0.3415660000   
9   Plot 6A Bukoto Crescent, Naguru, Kampala 11431... 0.3419140000   
10                   118 Luthuli Ave, Kampala, Uganda 0.3071250000   
11                  69-71 Buganda Rd, Kampala, Uganda 0.3249200000   
12  80, Plot 672, Hanlon Road, Nsambya Hill/P.O. B... 0.3007400000   
13              Plot 1 Kyadondo road, Kampala, Uganda 0.2883500000   
14  Plot M219 Nakawa Industrial Area, Inside UIRI,... 0.3378910000   
15  Office No 3, REGENCY PLAZA, 18 Lugogo By-Pass,... 0.3313330000   

             LON                              COORDINATES  \
0  32.5761710000     0.331245631028126, 32.57617147103373   
1  32.5761190000    0.3391550027171229, 32.57611913788221   
2  32.5675150000      0.33376643025242, 32.56751532874441   
3  32.5514940000  0.22726149143899727, 32.551493611083714   
4  32.5615450000   0.24710642516379605, 32.56154518525522   
5  32.5768040000    0.3244006304886406, 32.57680365762819   
6  32.5876990000   0.32677070175063294, 32.58769862875094   
7  32.5833240000    0.3279995303971809, 32.58332419987116   
8  32.5779390000  0.34156560138915515, 32.577938699857306   
9  32.6050250000     0.3419138946476636, 32.6050250521126   
10 32.6244090000   0.30712525960239967, 32.62440869986175   
11 32.5751340000   0.32492007311341675, 32.57513447097692   
12 32.5890170000  0.30073994493747824, 32.589017342090145   
13 32.5597390000    0.2883501600495953, 32.55973909986086   
14 32.6254010000   0.33789097348845115, 32.62540110209415   
15 32.6025240000    0.3313325589865815, 32.60252429988367   

                  NOTES          PRJ_LAT           PRJ_LON      t_node  \
0                  None 36613.6482006860 452838.7936172242  3799704477   
1                  None 37487.8549663987 452833.0450933628  7401202859   
2                  None 36892.2336127046 451875.5986544515  2297820937   
3                  None 25119.9449333336 450092.3882960156  2614743709   
4                  None 27313.4443953668 451210.9074285642  7062105534   
5                  None 35857.0460002950 452909.1994618282  6880975575   
6                  None 36118.9590743176 454121.5640353452  8193448456   
7                  None 36254.8242478438 453634.7367577547  7238684605   
8                  None 37754.3414306474 453035.5792187499  6232768975   
9                  None 37792.6787080598 456049.5983998349   560476404   
10                 None 33947.277966231

### Projected OSMNx graph for Kampala

In [10]:
import osmnx as ox, csv

ox.config(
    log_console=False, 
    use_cache=True, 
    log_file=True,
    overpass_endpoint='https://overpass-api.de/api/interpreter'
)

In [11]:
%%time
if 'G_proj_u' not in globals():
    # Load projected graph, G_proj
    g_projected_nodes = gpd.read_feather('data/g_projected_nodes.feather')
    g_projected_edges = gpd.read_feather('data/g_projected_edges.feather')
    G_proj = ox.utils_graph.graph_from_gdfs(g_projected_nodes, g_projected_edges)
    G_proj_u = ox.utils_graph.get_undirected(G_proj)
    
if 'G_u' not in globals():
    # Load projected graph, G_proj
    g_unprojected_nodes = gpd.read_feather('data/g_unprojected_nodes.feather')
    g_unprojected_edges = gpd.read_feather('data/g_unprojected_edges.feather')
    G = ox.utils_graph.graph_from_gdfs(g_unprojected_nodes, g_unprojected_edges)
    G_u = ox.utils_graph.get_undirected(G)

CPU times: user 3min 7s, sys: 2.86 s, total: 3min 10s
Wall time: 3min 11s


In [12]:
G_proj.graph['crs']

<Projected CRS: PROJCRS["unknown",BASEGEOGCRS["unknown",DATUM["Wor ...>
Name: unknown
Axis Info [cartesian]:
- E[east]: Easting (metre)
- N[north]: Northing (metre)
Area of Use:
- undefined
Coordinate Operation:
- name: UTM zone 36N
- method: Transverse Mercator
Datum: World Geodetic System 1984
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [13]:
G.graph['crs']

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

## Create residence-test facility pair DF and analysis columns

### D3 computation approaches

1. Method 1 (`d3_euc`) - Simple euclidean distance between closest node to a residence centroid and the closest node to a testing facility
2. Method 2 (`d3_path_sum`) - Sum of euclidean distances between nodes that constitute a path (same as Method 1 but euclidean distance is obtained for each node pair and then summed)
3. Method 3 (`d3_shapely`) - Total length of a Shapely LineString derived from list of coordinates that constitute a path
4. Method 4 (`d3_edge_attrs`) - Computed through OSMNx graph utils' route_edge_attributes function using "length" as weight

All methods, except Method 1, use the list of path nodes (path_node_list) generated from OSMNx shortest path function.

All methods, except Method 4, use a projected graph. 

References:

1. Method 1: https://osmnx.readthedocs.io/en/stable/osmnx.html#osmnx.distance.euclidean_dist_vec
2. Method 2: Same as Ref 1
3. Method 3: https://shapely.readthedocs.io/en/stable/manual.html
4. Method 4: https://github.com/gboeing/osmnx-examples/blob/main/notebooks/02-routing-speed-time.ipynb

### Create a Pandas DataFrame (`paired_df`) to store results of d1, d2, and d3 computation

Let's obtain a sample of residential units.

In [14]:
%%time
total_rows = 10
res_units_sample_gdf = residential_centroids_4326_gdf.sample(n=total_rows, random_state=1)

res_units_sample_gdf

CPU times: user 1.87 ms, sys: 288 µs, total: 2.16 ms
Wall time: 2.09 ms


parish_name     building          lat           lon          prj_lat  \
108      Kisugu        house 0.3108663004 32.6096398141 34360.8727358355   
206      Kisugu        house 0.3085059855 32.6077094105 34099.9887480836   
106      Kisugu   apartments 0.3097933467 32.6089452703 34242.2791634763   
107      Kisugu  residential 0.3099999500 32.6099464500 34265.1114668231   
51       Kisugu   apartments 0.3034337892 32.6058160064 33539.3529249087   
33       Kisugu  residential 0.3055204088 32.6049545740 33769.9961761353   
59       Kisugu  residential 0.3034706937 32.6066937764 33543.4285311180   
152      Kisugu  residential 0.3064853012 32.6091980710 33876.6310349672   
4        Kisugu  residential 0.3046784338 32.6080187078 33676.9179346887   
31       Kisugu  residential 0.3055534654 32.6059218690 33773.6460562803   

              prj_lon      r_node            d1            d1_euc  \
108 456562.9815281392   475033488 22.9457818662 457854.1532814049   
206 456348.1643899938   579993375 29.9726741560 457620.4282751550   
106 456485.6911287252   579993404 21.1503781451 457768.1944910321   
107 456597.0991967148  1583799787 15.8848284194 457880.9985778930   
51  456137.4533565310  8144996943 18.1240432856 457368.8495614924   
33  456041.6049933219   579992646 11.4231693408 457290.2340162331   
59  456235.1282905157  1623680456 28.3771980662 457466.5603996488   
152 456513.8083599660  1425900085 33.9219259997 457769.0283905182   
4   456382.5662585886  6227266299 29.8734513255 457623.4058550270   
31  456149.2418963615   579992650 24.0530212551 457397.8465740304   

      r_node_lat    r_node_lon          r_node_x         r_node_y  \
108 0.3109017000 32.6098430000 456585.5913781864 34364.7847156791   
206 0.3082407000 32.6077652000 456354.3713367001 34070.6658047005   
106 0.3097587000 32.6091322000 456506.4917735084 34238.4488015763   
107 0.3100471000 32.6100813000 456612.1049491421 34270.3225289032   
51  0.3033524000 32.6059574000 456153.1867502120 33530.3561883728   
33  0.3055115000 32.6048523000 456030.2243100812 33769.0118759969   
59  0.3034371000 32.6069466000 456263.2613652091 33539.7143046328   
152 0.3064335000 32.6088976000 456480.3729432435 33870.9065286898   
4   0.3045855000 32.6082708000 456410.6177021883 33666.6446875843   
31  0.3053494000 32.6058468000 456140.8876837517 33751.0904591220   

                     geometry  
108  POINT (32.60964 0.31087)  
206  POINT (32.60771 0.30851)  
106  POINT (32.60895 0.30979)  
107  POINT (32.60995 0.31000)  
51   POINT (32.60582 0.30343)  
33   POINT (32.60495 0.30552)  
59   POINT (32.60669 0.30347)  
152  POINT (32.60920 0.30649)  
4    POINT (32.60802 0.30468)  
31   POINT (32.60592 0.30555)

### `paired_df`: Using `oxtools` functions

In [15]:
from oxtools.compute_d3 import create_paired_df, compute_d3, compute_d3_loop

In [16]:
%%time
paired_df = create_paired_df(res_units_sample_gdf, filtered_testing_sites_4326_gdf)
paired_df = compute_d3_loop(paired_df, G_proj_u, G_u)

CPU times: user 28.3 s, sys: 879 ms, total: 29.2 s
Wall time: 29.2 s


### `paired_df`: Long way with more explanations (slower)

The earlier version of the code below is kept here in markdown format to explain what happens in the `oxtools` functions above.

```python
%%time
import networkx as nx, os
from tqdm import tqdm, notebook
from shapely.geometry import LineString


dict_list = []
df_list = []

# tqdm parameters
total_rows=5 #residential_centroids_4326_gdf.shape[0]

for r_index, r_row in tqdm(residential_centroids_4326_gdf.sample(n=total_rows, random_state=1).iterrows(), total=total_rows, desc='Residence Loop'):
    
    # for each sampled residence centroid, compute d3 and other parameters
    # create a dictionary for each pair and create a temporary DF for each dictionary
    dict_list = []
    for t_index, t_row in filtered_testing_sites_4326_gdf.iterrows():
        
        # 1. assemble the paired record using the nested loop
        r_parish_name = r_row['parish_name']
        r_node = r_row['r_node']
        r_node_lat = r_row['r_node_lat']
        r_node_lon = r_row['r_node_lon']
        t_node = t_row['t_node']
        t_node_lat = t_row['t_node_lat']
        t_node_lon = t_row['t_node_lon']
        d1 = r_row['d1']
        d2 = t_row['d2']
        
        # List if OSMNx nodes for shortest path
        path_node_list = ox.distance.shortest_path(G_proj, r_node, t_node, \
                                                   weight='length', cpus=2)

        ## d3 method 1 (sum of euclidean distance of path edges)
        # simplified explanation: 
        # 1. node to node distance: 
        #    osmnx.distance.euclidean_dist_vec(source_lat, source_lon, target_lat, 
        #        target_lon, distance)
        # 2. dist_list: list of node to node distances generated through Python list 
        #    comprehension (for loop)
        # 3. d3_path_sum: sum of distances in dist_list
        dist_list = [ ox.distance.euclidean_dist_vec(\
                    G_proj.nodes[path_node_list[i]]['y'], \
                    G_proj.nodes[path_node_list[i]]['x'], \
                    G_proj.nodes[path_node_list[i+1]]['y'], \
                    G_proj.nodes[path_node_list[i+1]]['x']) \
                    for i in range(len(path_node_list)-1) ]
        d3_path_sum = sum(dist_list)

        ## d3 method 2 (Shapely LineString Length)
        coords_list = [(G_proj.nodes[node]['x'], G_proj.nodes[node]['y']) \
                       for node in path_node_list ]
        path_line = LineString(coords_list)
        d3_shapely = path_line.length

        ## d3 method 3 (euclidean distance between residence centroid 
        #    and test facility coordinates
        d3_euc = ox.distance.euclidean_dist_vec(r_row['prj_lat'], r_row['prj_lon'], \
                                                t_row['PRJ_LAT'], t_row['PRJ_LON'])
        
        ## d3 method 4 (sum of lengths of edges through OSMNx edge attributes
        d3_edge_attrs = sum(ox.utils_graph.get_route_edge_attributes(G, \
                                  path_node_list, "length"))
        
        # obtain d_total
        d_total = d1 + d2 + d3_edge_attrs
        
        # assemble record dictionary
        record_dict = {
            'parish_name': r_parish_name,
            'r_node': r_node,
            'r_node_lat': r_node_lat,
            'r_node_lon': r_node_lon,
            't_node': t_node,
            't_node_lat': t_node_lat,
            't_node_lon': t_node_lon,
            'd3_euc': d3_euc,
            'd3_shapely': d3_shapely,
            'path_node_list': path_node_list,
            'path_distances': dist_list,
            'd3_path_sum': d3_path_sum,
            'd3_edge_attrs': d3_edge_attrs,
            'd_total': d_total
        }
        #print(record_dict)
        
        # append record dict to dict_list (each record is a future DF 
        #   row, each dict_list is future temp DF)
        dict_list.append(record_dict)
    
    # 2. Create a temporary DF to store list of record 
    #    dictionaries (these become DF rows)
    # Sort values by the d3_path_sum column
    # Group by r_node (remember each temp DF contains records for only one r_node)
    # Retain the first record (which would have the smallest value of d_total)
    df = pd.DataFrame(dict_list).sort_values(by=['d_total'])\
            .groupby(['r_node'], as_index=False).first()
    # append this temp DF to a DF list
    df_list.append(df)

# 3. Concatenate (combine) all the temp DFs in the DF list to a single DF
# Reset the index of the DF and drop the original indices of the temp DFs
paired_df = pd.concat(df_list).reset_index(drop=True)

# 4. Convert the path_node_list column to type string
paired_df['path_node_list'] = paired_df['path_node_list'].astype(str)

paired_df
```

In [17]:
paired_df

r_node parish_name   r_node_lat    r_node_lon          prj_lat  \
0   475033488      Kisugu 0.3109017000 32.6098430000 34360.8727358355   
1   579992646      Kisugu 0.3055115000 32.6048523000 33769.9961761353   
2   579992650      Kisugu 0.3053494000 32.6058468000 33773.6460562803   
3   579993375      Kisugu 0.3082407000 32.6077652000 34099.9887480836   
4   579993404      Kisugu 0.3097587000 32.6091322000 34242.2791634763   
5  1425900085      Kisugu 0.3064335000 32.6088976000 33876.6310349672   
6  1583799787      Kisugu 0.3100471000 32.6100813000 34265.1114668231   
7  1623680456      Kisugu 0.3034371000 32.6069466000 33543.4285311180   
8  6227266299      Kisugu 0.3045855000 32.6082708000 33676.9179346887   
9  8144996943      Kisugu 0.3033524000 32.6059574000 33539.3529249087   

            prj_lon      t_node   t_node_lat    t_node_lon          PRJ_LAT  \
0 456562.9815281392  7401065633 0.3076673000 32.6249390000 33947.2779662314   
1 456041.6049933219  8003448502 0.3007283000 32.5890897000 33241.6700525009   
2 456149.2418963615  8003448502 0.3007283000 32.5890897000 33241.6700525009   
3 456348.1643899938  7401065633 0.3076673000 32.6249390000 33947.2779662314   
4 456485.6911287252  7401065633 0.3076673000 32.6249390000 33947.2779662314   
5 456513.8083599660  7401065633 0.3076673000 32.6249390000 33947.2779662314   
6 456597.0991967148  7401065633 0.3076673000 32.6249390000 33947.2779662314   
7 456235.1282905157  8003448502 0.3007283000 32.5890897000 33241.6700525009   
8 456382.5662585886  8003448502 0.3007283000 32.5890897000 33241.6700525009   
9 456137.4533565310  8003448502 0.3007283000 32.5890897000 33241.6700525009   

            PRJ_LON            d1            d2  \
0 458206.4204631053 22.9457818662 84.0904376390   
1 454268.1128570444 11.4231693408  8.1925049479   
2 454268.1128570444 24.0530212551  8.1925049479   
3 458206.4204631053 29.9726741560 84.0904376390   
4 458206.4204631053 21.1503781451 84.0904376390   
5 458206.4204631053 33.9219259997 84.0904376390   
6 458206.4204631053 15.8848284194 84.0904376390   
7 454268.1128570444 28.3771980662  8.1925049479   
8 454268.1128570444 29.8734513255  8.1925049479   
9 454268.1128570444 18.1240432856  8.1925049479   

                                      path_node_list          d3_euc  \
0  [475033488, 1583799847, 475033491, 3481960627,... 1694.6835003641   
1  [579992646, 6226995197, 8145150031, 6226995198... 1850.5142124157   
2  [579992650, 6226995049, 6226995048, 6226995046... 1954.9027932762   
3  [579993375, 579993374, 579993373, 6226994993, ... 1864.5203716102   
4  [579993404, 1583799967, 1583799788, 1583799935... 1745.8336543244   
5  [1425900085, 1425899988, 1425900082, 579993366... 1694.0858067379   
6  [1583799787, 6227589978, 1583800118, 158380034... 1640.4063742119   
7  [1623680456, 6227266310, 6227266309, 622726630... 1990.0271090947   
8  [6227266299, 6227266298, 579993288, 6227266296... 2158.7852848884   
9  [8144996943, 8144996944, 579992620, 579992609,... 1892.8943434713   

      d3_path_sum      d3_shapely   d3_edge_attrs         d_total  
0 2614.8427705889 2614.8427705889 2619.6160000000 2726.6522195052  
1 2846.9235105639 2846.9235105639 2851.0360000000 2870.6516742886  
2 2955.3941319221 2955.3941319221 2958.5650000000 2990.8105262029  
3 3028.3221787246 3028.3221787246 3033.9270000000 3147.9901117949  
4 2727.5351567984 2727.5351567984 2732.6070000000 2837.8478157841  
5 3227.4703833402 3227.4703833402 3234.1250000000 3352.1373636386  
6 2674.0149068306 2674.0149068306 2679.0010000000 2778.9762660583  
7 2968.3358163695 2968.3358163695 2970.9040000000 3007.4737030141  
8 2988.6203467860 2988.6203467860 2991.7800000000 3029.8459562733  
9 2755.7231849327 2755.7231849327 2758.1140000000 2784.4305482335

### Questions:

1. What are the differences among the three methods to compute for d3?
2. How will the euclidean method for measuring d3 differ from a network based measure?

## Map Paired Residence Centroids and Test Facilities and Node-to-Node Routes

In [21]:
%%time
import folium, json
from folium import plugins

map1 = filtered_testing_sites_4326_gdf.explore(marker_kwds=dict(radius=5))

# Tile Layer (can add more, these become radio buttons on Layer Control)
folium.TileLayer('cartodbpositron').add_to(map1)
folium.TileLayer('cartodbdark_matter').add_to(map1)

# Feature groups become checkboxes in Layer Control Widget
fg1=folium.FeatureGroup(name='Residences', show=True)
fg2=folium.FeatureGroup(name='Residence Nodes', show=True)
fg3=folium.FeatureGroup(name='Residence to Node', show=True)

# Residences, Nodes and Residence-to-Node Paths
for row in residential_centroids_4326_gdf.itertuples():

    folium.CircleMarker(
                    location=[row.lat,row.lon], \
                    radius=4, \
                    color='black', \
                    weight=1, \
                    fill=True, \
                    fill_color='red', \
                    fill_opacity=1).add_to(fg1)


    folium.CircleMarker(
                    location=[row.r_node_lat,row.r_node_lon], \
                    radius=4, \
                    color='black', \
                    weight=1, \
                    fill=True, \
                    fill_color='yellow', \
                    fill_opacity=1).add_to(fg2)
    
    r_line_points = ((row.lat,row.lon),(row.r_node_lat,row.r_node_lon))
    popup_d1 = folium.Popup('d1: '+str(row.d1)+' meters')
    folium.PolyLine(r_line_points,
                    color='gray',
                    popup=popup_d1,
                    weight=2,
                    opacity=0.8
                   ).add_to(fg3)

fg1.add_to(map1)
fg2.add_to(map1)
fg3.add_to(map1)

# Residences, Nodes and Residence-to-Node Paths
fg4=folium.FeatureGroup(name='Testing Sites', show=True)
fg5=folium.FeatureGroup(name='Testing Site Nodes', show=True)
fg6=folium.FeatureGroup(name='Testing Site to Node', show=True)

for row in filtered_testing_sites_4326_gdf.itertuples():

    folium.CircleMarker(
                    location=[row.LAT,row.LON], \
                    radius=4, \
                    color='black', \
                    weight=1, \
                    fill=True, \
                    fill_color='blue', \
                    fill_opacity=1).add_to(fg4)


    folium.CircleMarker(
                    location=[row.t_node_lat,row.t_node_lon], \
                    radius=4, \
                    color='black', \
                    weight=1, \
                    fill=True, \
                    fill_color='yellow', \
                    fill_opacity=1).add_to(fg5)
    
    t_line_points = ((row.LAT,row.LON),(row.t_node_lat,row.t_node_lon))
    popup_d2 = folium.Popup('d2: '+str(row.d2)+' meters')
    folium.PolyLine(t_line_points,
                    color='gray',
                    popup=popup_d2,
                    weight=2,
                    opacity=0.8
                   ).add_to(fg6)
fg4.add_to(map1)
fg5.add_to(map1)
fg6.add_to(map1)

# Node to Node Routes
fg7=folium.FeatureGroup(name='Node to Node Routes', show=True)
for row in paired_df.itertuples():
    #path_string = row['path_node_list']
    #path_node_list = json.loads(path_string)
    edge_list = []
    #path_node_list = row.path_node_list
    path_node_list = [ int(item.strip()) for item in str(row.path_node_list).strip('[]').split(',') ]
    for i in range(len(path_node_list)-1):
        edge_pair = ((G_proj.nodes[path_node_list[i]]['lat'], G_proj.nodes[path_node_list[i]]['lon']), \
                     (G_proj.nodes[path_node_list[i+1]]['lat'], G_proj.nodes[path_node_list[i+1]]['lon']))
        edge_list.append(edge_pair)
        popup = folium.Popup('d_total: '+str(row.d_total/1000)+' km')
        folium.PolyLine(edge_list,
                        color='red',
                        weight=2,
                        opacity=0.8,
                        popup=popup
                       ).add_to(fg7)
fg7.add_to(map1)

# GeoJSON parish boundary with style function
fg8=folium.FeatureGroup(name='Parish Boundary', show=True)
parish_name = ''.join(paired_df['parish_name'].unique())
style_function = lambda x: {'fillColor': '#ffffff', 
                            'color':'#000000', 
                            'fillOpacity': 0, 
                            'weight': 3}
geojson = folium.GeoJson(
    data=parish_gdf['geometry'], 
    name="geojson",
    style_function=style_function
)
geojson.add_child(folium.Popup('Parish Boundary: '+parish_name))
geojson.add_to(fg8)
fg8.add_to(map1)

# Let's give the user the option to turn this feature group on (set it to False).
#  This feature group overlaps with feature group 8.
fg9=folium.FeatureGroup(name='Parishes', show=False)
for r in parishes_gdf.itertuples():
    # Simplify the representation of the parishes
    #    so the polygons display easily
    sim_geo = gpd.GeoSeries(r.geometry).simplify(tolerance=0.00001)
    # convert the simplified geometry to GeoJSON
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'color':'black','weight':2, 'fillColor': 'orange','fillOpacity':0.05},
                           highlight_function=lambda x: {'color':'black','weight':2, 'fillColor': 'blue','fillOpacity':0.075})
    # prepare the popup for each parish (name and area in sq m)
    folium.Popup('Parish: '+r.NAME_4+'<br/>'+'Area (sq. m.): '+str(r.area_sqm)).add_to(geo_j)
    geo_j.add_to(fg9)
fg9.add_to(map1)

# The following are map controls:
# 1. Layer Control
folium.LayerControl(position='topright', collapsed=True, autoZIndex=True).add_to(map1)
# 2. Measure Control
map1.add_child(plugins.MeasureControl(activecolor = "blue", completedcolor = "black",))
# 3. Full Screen button
plugins.Fullscreen(
    position='topright',
    title='Expand me',
    title_cancel='Exit me',
    force_separate_button=True
).add_to(map1)

map1

CPU times: user 1.84 s, sys: 20 ms, total: 1.86 s
Wall time: 1.86 s


## Housekeeping

In [22]:
paired_df.to_pickle('data/paired_df.pickle')

In [23]:
if os.path.exists('data/paired_cache_df.pickle'):
    paired_cache_df = pd.read_pickle('data/paired_cache_df.pickle')
else:
    paired_cache_df = pd.DataFrame()

if (paired_cache_df.empty) or (parish_name not in paired_cache_df['parish_name'].values):
    paired_cache_df = paired_cache_df.append(paired_df, ignore_index=True)
    paired_cache_df.to_pickle('data/paired_cache_df.pickle')

paired_cache_df['parish_name'].unique()

array(['Kisugu', 'Kawempe I', 'Kazo Ward', 'Bwaise I', 'Bwaise Ii',
       'Bwaise Iii', 'Makerere Iii', 'Kanyanya'], dtype=object)